# 📈 Lineární regrese

# Knihovny

In [1]:
import pandas as pd
import numpy as np

from plotly import graph_objects as go
import plotly.express as px

np.set_printoptions(precision=5, suppress=True)  # suppress scientific float notation (so 0.000 is printed as 0.)

In [2]:
def plot_prediction_results(title, true, predicted):
    from sklearn.metrics import mean_squared_error
    fig = go.Figure(data=go.Scatter(x=[0, 60], y=[0, 60], mode="lines", name="y = ŷ"))
    fig.add_scatter(x=true, y=predicted, name="test, prediction", mode="markers")
    fig.update_layout(
        title=f"Visualization of predictions | {title} | RMSE: {np.sqrt(mean_squared_error(Yth, np.array(Y_test)))}",
        xaxis_title="Real values",
        yaxis_title="Predicted values",
        
    )

    fig.update_layout(yaxis=dict(range=[0,50],  scaleratio=1));
    fig.update_layout(xaxis=dict(range=[0,50],  scaleratio=1));
    fig.show()

## Načtení dat




Využijeme data ze serveru Kaggle o cenách domů v oblasti Bostonu v USA [více info zde](https://www.kaggle.com/c/boston-housing).

Data jsou již vyčištěná. Proměnná, kterou chceme predikovat je `medv`.

In [3]:
df = pd.read_csv('boston.csv')
print('Shape', df.shape)
df.head()

Shape (333, 15)


ID     crim    zn  indus  chas    nox     rm   age     dis  rad  tax  \
0   1  0.00632  18.0   2.31     0  0.538  6.575  65.2  4.0900    1  296   
1   2  0.02731   0.0   7.07     0  0.469  6.421  78.9  4.9671    2  242   
2   4  0.03237   0.0   2.18     0  0.458  6.998  45.8  6.0622    3  222   
3   5  0.06905   0.0   2.18     0  0.458  7.147  54.2  6.0622    3  222   
4   7  0.08829  12.5   7.87     0  0.524  6.012  66.6  5.5605    5  311   

   ptratio   black  lstat  medv  
0     15.3  396.90   4.98  24.0  
1     17.8  396.90   9.14  21.6  
2     18.7  394.63   2.94  33.4  
3     18.7  396.90   5.33  36.2  
4     15.2  395.60  12.43  22.9

### Příprava trénovací a testovací množiny

Využijeme [train_test_split](https://scikit-learn.org/stable/modules/generated/sklearn.model_selection.train_test_split.html) ze `scikit-learn`.

In [4]:
from sklearn.model_selection import train_test_split

X, X_test, Y, Y_test = train_test_split(
    df.drop(columns=["ID", "medv"]), df["medv"], test_size=0.25, random_state=42
)
print("Train X shape", X.shape)
print("Test X shape", X_test.shape)

Train X shape (249, 13)
Test X shape (84, 13)


# Rekapitulace


Lineární regrese s jedním příznakem:

$$\boldsymbol{y} = \boldsymbol{w_1 x_1}+ \boldsymbol{w_0}$$
Kde:
- $\boldsymbol{w_0}$ je intercept
- $\boldsymbol{wx}$ je  slope

A dá se také zapsat jako 

$$ \boldsymbol{y} = \boldsymbol{w_{0}} + \boldsymbol{w_1 x_1} + \epsilon$$

$$ \boldsymbol{y} = \boldsymbol{w_0} + \boldsymbol{w_1 x_1} + ... + \boldsymbol{w_n x_n} + \epsilon$$

Velice p2knou a interaktivní vizualizaci najdete [zde](https://setosa.io/ev/ordinary-least-squares-regression).

# ✍️ Lineární regrese - by hand

## Task

Používejte pouze maticové operace v [numpy.linalg](https://docs.scipy.org/doc/numpy-1.15.1/reference/routines.linalg.html).

* Vypočtěte odhad $\hat{\boldsymbol w}_{OLS} = (\mathbf{X}^T \mathbf X)^{-1} \mathbf X^T \boldsymbol Y$ a vypište jednotlivé koeficienty.
* Spočtěte hodnotu $\text{RSS}(\hat{\boldsymbol w}_{OLS}) = \lVert \boldsymbol Y - \mathbf X \boldsymbol w \rVert^2$.
* Pro testovací data proveďte predikce $\hat Y_i$ a porovnejte je se skutečnými hodnotami $Y_i$.
Jako míru porovnání použijte RMSE - root mean squared error definovanou pomocí vztahu $\text{RMSE} = \sqrt{\sum_{i}(Y_i - \hat Y_i)^2}$. Můžete použít implementaci [sklearn.metrics.mean_squared_error](https://scikit-learn.org/stable/modules/generated/sklearn.metrics.mean_squared_error.html#sklearn.metrics.mean_squared_error)
* Nakreslete scatter plot hodnot $Y_i$ a $\hat Y_i$ pro testovací množinu.


## Ordinary least squares

* Vypočtěte odhad $\hat{\boldsymbol w}_{OLS} = (\mathbf{X}^T \mathbf X)^{-1} \mathbf X^T \boldsymbol Y$ a vypište jednotlivé koeficienty.


$\text{Normální rovnice :}$ $$  \mathbf{X}^T\boldsymbol{Y}−\mathbf{X}^T\boldsymbol{Xw}= 0⇔\mathbf{X}^T \mathbf{X} \boldsymbol{w} =\mathbf{X}^T \boldsymbol{Y} $$

In [5]:
XX = np.matrix(
    np.concatenate(
        [np.ones((X.shape[0], 1)),
         np.array(X)], axis=1))
print(XX.shape)

(249, 14)


In [6]:
XX[0,:]

matrix([[  1.    ,  15.0234,   0.    ,  18.1   ,   0.    ,   0.614 ,
           5.304 ,  97.3   ,   2.1007,  24.    , 666.    ,  20.2   ,
         349.48  ,  24.91  ]])

In [7]:
X.head(1)

crim   zn  indus  chas    nox     rm   age     dis  rad  tax  ptratio  \
313  15.0234  0.0   18.1     0  0.614  5.304  97.3  2.1007   24  666     20.2   

      black  lstat  
313  349.48  24.91

$$\hat{\boldsymbol w}_{OLS} = (\mathbf{X}^T \mathbf X)^{-1} \mathbf X^T \boldsymbol Y$$

In [8]:
YY = np.matrix(Y).T
YY.shape

w_hat = (XX.T*XX).I * XX.T*YY
w_hat.shape

print(w_hat.T)

[[ 38.20659  -0.07709   0.05966  -0.01475   4.1967  -16.86474   3.55901
   -0.01256  -1.81433   0.40758  -0.01564  -0.77078   0.00752  -0.58124]]


In [9]:
np.array([1]+[0 for x in range(13)])*w_hat

matrix([[38.20659]])

## Residual sum of squares

* Spočtěte hodnotu $\text{RSS}(\hat{\boldsymbol w}_{OLS}) = \lVert \boldsymbol Y - \mathbf X \boldsymbol w \rVert^2$.

In [10]:
 print(f'RSS: {np.linalg.norm(YY - XX*w_hat)**2}')

RSS: 5649.69059873862


In [11]:
print(f'The same RSS: {((YY - XX*w_hat).T*(YY - XX*w_hat))[0,0]}')

The same RSS: 5649.69059873862


## Root mean squared error

* Pro testovací data proveďte predikce $\hat Y_i$ a porovnejte je se skutečnými hodnotami $Y_i$.
Jako míru porovnání použijte RMSE - root mean squared error definovanou pomocí vztahu $\text{RMSE} = \sqrt{\sum_{i}(Y_i - \hat Y_i)^2}$. Můžete použít implementaci [sklearn.metrics.mean_squared_error](https://scikit-learn.org/stable/modules/generated/sklearn.metrics.mean_squared_error.html#sklearn.metrics.mean_squared_error)

In [12]:
XXt = np.matrix(np.concatenate([np.ones((X_test.shape[0],1)),np.array(X_test)], axis = 1))

In [13]:
Yt_hat = XXt*w_hat

In [14]:
Yth = np.array(Yt_hat).flatten() # flatten převede n jednodimenzionálních do 1 n-dimenzionálního vektoru 

In [15]:
# error
Yth - np.array(Y_test)
# squared error
(Yth - np.array(Y_test)) ** 2
# mean squared error
((Yth - np.array(Y_test)) ** 2).mean()
# root mean squared error
np.sqrt( ( (Yth - np.array(Y_test)) ** 2).mean())
print(f'RMSE: {np.sqrt( ( (Yth - np.array(Y_test)) ** 2).mean())}')

RMSE: 4.799532488947229


## Vizualizace $Y_i$ a $\hat Y_i$

* Nakreslete scatter plot hodnot $Y_i$ a $\hat Y_i$ pro testovací množinu.

In [16]:
plot_prediction_results("Our Linear Regression", Y_test, Yth)

# 📦 Lineární regrese pomocí *scikit-learn*

## Task - zopakujte metodu nejmenších čtverců s využitím scikit-learn

* Zopakujte postup z předchozího bodu s využitím třídy [LinearRegression](https://scikit-learn.org/stable/modules/generated/sklearn.linear_model.LinearRegression.html#sklearn.linear_model.LinearRegression) ze `scikit-learn`.
* Porovnejte výsledky s předchozím manuálním přístupem.

In [17]:
from sklearn.linear_model import LinearRegression
clf = LinearRegression()
clf.fit(X,Y)

LinearRegression(copy_X=True, fit_intercept=True, n_jobs=None, normalize=False)

In [18]:
print(clf.coef_)

[ -0.07709   0.05966  -0.01475   4.1967  -16.86474   3.55901  -0.01256
  -1.81433   0.40758  -0.01564  -0.77078   0.00752  -0.58124]


In [19]:
print(*np.asarray(w_hat[1:, :].T))

[ -0.07709   0.05966  -0.01475   4.1967  -16.86474   3.55901  -0.01256
  -1.81433   0.40758  -0.01564  -0.77078   0.00752  -0.58124]


## Predikce 

In [20]:
Yth = clf.predict(X_test)

## RMSE a RSS

In [21]:
print('The same RSS', ((YY - XX*w_hat).T*(YY - XX*w_hat))[0,0])

The same RSS 5649.69059873862


In [22]:
from sklearn.metrics import mean_squared_error
print('RMSE:', np.sqrt(mean_squared_error(Yth, np.array(Y_test))))

RMSE: 4.799532488947336


## Vizualizace $Y_i$ a $\hat Y_i$

In [23]:
plot_prediction_results("sklearn linear regression", Y_test, Yth)

# Gradientní sestup (gradient descent)

## Parciálna derivácia
Parciálna derivácia je derivácia funkcie viacerých premenných 

podľa jednej z týchto premenných.

Funkcia $f(x,y) = x^2 + y^2$ má dve parciálne derivácie:
* $\frac{\partial f}{\partial x}$ - parciálna derivácia podľa x
* $\frac{\partial f}{\partial y}$ - parciálna derivácia podľa y

$$\frac{\partial f}{\partial x} (x^2 + y^2) = 2x$$


$$\frac{\partial f}{\partial y} (x^2 + y^2) = 2y$$

## Gradient
Gradient funkcie f v bode $b\in{D_f}$ je vektor 
$$\nabla f(b) = (\frac{\partial f}{\partial x_1}(b), \frac{\partial f}{\partial x_2}(b), ... \frac{\partial f}{\partial x_n}(b))$$

V našom prípade platí
$$f(x,y) = x^2 + y^2$$

$$\nabla f(x,y) = (\frac{\partial f}{\partial x}, \frac{\partial f}{\partial y}) = (2x, 2y)$$

$$\nabla f(1,1) = (2,2)$$

### Update váh pomocou gradientu:
$$w^{(i+1)} = w^{(i)} - \alpha \nabla RSS(w^{(i)}) = w^{(i)} -\alpha 2 \mathbf{X}^T ( \boldsymbol Y - \mathbf X \boldsymbol{w})$$

## Task 3 - proveďte metodu nejmenších čtverců pomocí gradientního sestupu

* Ručně implementujte gradientní sestup pro hledání $\boldsymbol w$ minimalizujícího $\text{RSS}(\boldsymbol w)$. Gradient je: $\nabla\text{RSS}(\boldsymbol{w}) = -2 \mathbf{X}^T ( \boldsymbol Y - \mathbf X \boldsymbol{w})$.
* Výsledný odhad $\hat{\boldsymbol w}$ porovnejte s $\hat{\boldsymbol w}_{OLS}$ získaným v předchozím bodě.

In [24]:
XX = np.matrix(np.concatenate([np.ones((X.shape[0],1)),np.array(X)], axis = 1))
YY = np.matrix(Y).T

max_iter  = 100000
alpha = 0.00000001

In [25]:
w = np.zeros([XX.shape[1],1])

for i in range(max_iter):
    grad = -2*XX.T*(YY - XX*w)
    w = w - alpha*grad

print(w.T)

[[ 0.16183 -0.02022  0.09503 -0.03325  0.18323  0.07363  1.65397  0.06535
  -0.2358   0.238   -0.01182  0.61621  0.02356 -0.77434]]


In [26]:
XXt = np.matrix(np.concatenate([np.ones((X_test.shape[0],1)),np.array(X_test)], axis = 1))
Yt_hat = XXt*w
Yth = np.array(Yt_hat).flatten()

In [27]:
plot_prediction_results(" gradient descent", Y_test, Yth)

## Task 4 - zopakujte Task 3 s tím, že nejprve standardizujete příznaky

Výsledky porovnejte s předchozími.

### Normalizácia

$$x_{normalized} = \frac{x - x_{min}}{x_{max} - x_{min}}$$

### Štandardizácia

$$x_{standardized} = \frac{x - mean}{std}$$

In [28]:
from sklearn.preprocessing import StandardScaler
scaler = StandardScaler()
scaler.fit(X)
X2 = scaler.transform(X)
X2_test = scaler.transform(X_test)

In [29]:
XX = np.matrix(np.concatenate([np.ones((X.shape[0],1)),np.array(X2)], axis = 1))
YY = np.matrix(Y).T

max_iter  = 20000
alpha = 0.0001

In [30]:
w = np.zeros([XX.shape[1],1])

for i in range(max_iter):
    grad = -2*XX.T*(YY - XX*w)
    w = w - alpha*grad

print(w.T)

[[22.88916 -0.57299  1.44468 -0.10095  1.02907 -2.00221  2.43519 -0.35408
  -3.66577  3.54586 -2.63274 -1.59352  0.62006 -4.10405]]


In [31]:
XXt = np.matrix(np.concatenate([np.ones((X_test.shape[0],1)),np.array(X2_test)], axis = 1))
Yt_hat = XXt*w
Yth = np.array(Yt_hat).flatten()

In [32]:
plot_prediction_results("gradient descent + standardization", Y_test, Yth)

In [33]:
clf = LinearRegression()
clf.fit(X2,Y)
print(clf.coef_)
print(clf.intercept_)

Yth = clf.predict(X2_test)

[-0.57299  1.44468 -0.10095  1.02907 -2.00221  2.43519 -0.35408 -3.66577
  3.54586 -2.63274 -1.59352  0.62006 -4.10405]
22.889156626506026


In [34]:
plot_prediction_results("sklearn + standardization", Y_test, Yth)